# Capstone Project - The Battle of Neighbourhoods (Week 1 & 2)
<h2><center>Property Prices & Venue Data Analysis of London</center></h2>


## 1. Introduction

### 1.1. Background
It goes without saying that the coronavirus (COVID-19) has had, is currently and will continue to have a significant impact on businesses and the economy worldwide. This is evident with stock market and oil prices crash, record breaking number of people filing for unemployment and major airlines on the brink of adminstration.

The Real Estate & Property market is no exception to the coronavirus impact, with the London property market coming to a halt back in March when the full lock down was announced to prevent the spread of the virus. Physical viewings were postponed, constructions were suspended and estate agents & morgage lenders no longer able to value properties in person.

As a result Zoopla has predicted that completed sales in the UK will be 50% lower in 2020 than in 2019 and Knight Frank has also predicted that the number of sales in Greater London will fall by 35%. However despite the bleak outlook for property and housing prices this year, a large number of firms & their analysts believe that the housing market could make a very strong recovery by 2021, with an estimated range of 3% - 6%.

### 1.2. Business Problem
The best decisions are often backed up by insight and data,  by utilising Machine Learning we can effectively and efficiently generate those insights in order to provide potential home-buyers and investors the best decision making support as possible. This brings us to our business problem: How can we generate insight so home-buyers and investors can make well informed choices when purchasing properties in London, especially in this uncertain economic situation?

In order to solve this business problem, we will cluster the London areas based on the average sales price, local venues and amenities, i.e. schools, supermarkets, coffee shops. We will then compare these clusters with the average property prices and rental prices for each borough, and also calculate the rental yield for each cluster for investors who are buying to let. This will provide valuable information on whether a property is a viable choice for home-buyers & investors.

## 2. Data Acquisition

### 2.1. Data Sources

The Price Paid Data (property sales data) in London will be sourced from HM Land REgistry, where the data is based on the raw data released each month. The dataset will include the following columns: Transaction unique identifier, Price, Date of Transfer, Postcode, Property Type, Old/New, Duration, PAON (Primary Addressable Object Name), SAON (Secondary Addressable Object Name), Street, Locality, Town/City, District, County and PPD Category Type.

The FourSquare API will be used to access and explore venues and amenities based on the Latitude and Longitude collected using the GeoCoder library, which will then be read into a dataframe for data wrangling and cleaning. This dataframe will be merged with the Price Paid Data from HM Land Registry and processed to be suitable for fitting the machine learning model.

The list of boroughs in London will be scrapped from the Wikipedia page and the average property and rental prices per borough will be scraped from Foxtons (A UK estate agency). The data will be visualised using Folium in order to gauge the recommendations generated by our model against average prices for each cluster.

Please see the References section at the end of the notebook for links and descriptions for data sources.

### 2.2. Data Collecting & Cleaning

In [1]:
import pandas as pd
import numpy as np
import json
import csv
import re
from bs4 import BeautifulSoup
from geopy.geocoders import Nominatim

import requests

import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import matplotlib.colors as colors

from sklearn.cluster import KMeans

import folium
import plotly.express as px
print('Libraries imported.')

Libraries imported.


#### Price Paid Data

In [2]:
ppd_2019 = pd.read_csv('../data/external/pp-2019.csv')
ppd_2019.head()

{8F1B26BD-60CA-53DB-E053-6C04A8C03649}  221950  2019-04-26 00:00  TS17 5FF  \
0  {8F1B26BD-60CB-53DB-E053-6C04A8C03649}  246995  2019-03-29 00:00  TS15 9ZH   
1  {8F1B26BD-60CC-53DB-E053-6C04A8C03649}  244950  2019-05-17 00:00  TS18 2FN   
2  {8F1B26BD-60CD-53DB-E053-6C04A8C03649}  139950  2019-05-31 00:00  TS18 2FN   
3  {8F1B26BD-60CE-53DB-E053-6C04A8C03649}  271995  2019-05-31 00:00  TS15 9FD   
4  {8F1B26BD-60CF-53DB-E053-6C04A8C03649}   84450  2019-04-26 00:00  TS18 2FD   

   D  Y  F    3 Unnamed: 8 CARRAWBURGH ROAD INGLEBY BARWICK  STOCKTON-ON-TEES  \
0  D  Y  F   16        NaN    GRESLEY CLOSE             NaN              YARM   
1  T  Y  F   13        NaN    INFINITY VIEW             NaN  STOCKTON-ON-TEES   
2  S  Y  F   40        NaN    INFINITY VIEW             NaN  STOCKTON-ON-TEES   
3  D  Y  F   27        NaN    MALLARD DRIVE             NaN              YARM   
4  T  Y  F  117        NaN  DEEPDALE AVENUE             NaN  STOCKTON-ON-TEES   

  STOCKTON-ON-TEES.1 STOCKTON-ON-TEES.2  A A.1  
0   STOCKTON-ON-TEES   STOCKTON-ON-TEES  A   A  
1   STOCKTON-ON-TEES   STOCKTON-ON-TEES  A   A  
2   STOCKTON-ON-TEES   STOCKTON-ON-TEES  A   A  
3   STOCKTON-ON-TEES   STOCKTON-ON-TEES  A   A  
4   STOCKTON-ON-TEES   STOCKTON-ON-TEES  A   A

As mentioned on the 'How to access HM Land Registry Price Paid Data' website, the column headers are not supplied in the file therefore they will need to be manually added.

In [3]:
ppd_2019.columns = ['TUID', 'Price', 'Date_of_Transfer', 'Postcode', 'Property_Type', 'Old_New', 'Duration',
                    'PAON', 'SAON', 'Street', 'Locality', 'Town_City', 'District', 'County', 'PPD_Cat_Type', 'Record_Status']

ppd_2019.sort_values(by=['Date_of_Transfer'], ascending=False, inplace=True)
ppd_2019.head()

TUID     Price  Date_of_Transfer  \
908444  {9DBAD222-BE41-6EB3-E053-6B04A8C0F257}    155000  2019-12-31 00:00   
415790  {9DBAD222-8F5A-6EB3-E053-6B04A8C0F257}  19476811  2019-12-31 00:00   
921591  {A2479555-56B8-74C7-E053-6B04A8C0887D}    294000  2019-12-31 00:00   
902369  {9DBAD222-B849-6EB3-E053-6B04A8C0F257}     67500  2019-12-31 00:00   
885654  {9FF0D969-B57B-11ED-E053-6C04A8C06383}    176000  2019-12-31 00:00   

        Postcode Property_Type Old_New Duration  \
908444  LS28 8ED             S       N        F   
415790   WA5 3UZ             O       N        L   
921591  SP11 6ZQ             T       Y        F   
902369  SA11 2HG             T       N        F   
885654   M46 9EF             S       N        L   

                                    PAON SAON                Street  \
908444                               445  NaN         BRADFORD ROAD   
415790  NORTH WEST FIRE & CONTROL CENTRE  NaN  LINGLEY GREEN AVENUE   
921591                                50  NaN        CASHMERE DRIVE   
902369                                10  NaN     PENRHIWTYN STREET   
885654                                43  NaN       CHANTERS AVENUE   

                          Locality   Town_City           District  \
908444                         NaN      PUDSEY              LEEDS   
415790  LINGLEY MERE BUSINESS PARK  WARRINGTON         WARRINGTON   
921591                         NaN     ANDOVER        TEST VALLEY   
902369                         NaN       NEATH  NEATH PORT TALBOT   
885654                    ATHERTON  MANCHESTER              WIGAN   

                    County PPD_Cat_Type Record_Status  
908444      WEST YORKSHIRE            B             A  
415790          WARRINGTON            B             A  
921591           HAMPSHIRE            A             A  
902369   NEATH PORT TALBOT            B             A  
885654  GREATER MANCHESTER            A             A

#### List of London Boroughs

In [4]:
source = requests.get('https://en.wikipedia.org/wiki/List_of_London_boroughs').text
soup = BeautifulSoup(source)
table = soup.find('table',class_='wikitable sortable')
tr_elements = soup.find_all(['tr'])[0:34]

# Write the table headers and cells into a CSV
with open('../data/raw/london_boroughs.csv', 'w', newline='', encoding='utf-8') as f:
    column_headers = ['Borough','Inner','Status', 'Local authority', 'Political control',
                      'Headquarters', 'Area (sq_mi)', 'Population (2013_est)', 'Coordinates', 'Nr in map']
    writer = csv.writer(f)
    writer.writerow(column_headers)
    for cell in tr_elements:
            td = cell.find_all('td')
            row = [i.text.replace('\n','').replace(' / ',',') for i in td]
            writer.writerow(row)

There were 3 boroughs that were scraped with citation reference text, '[note #]', so those were removed by chaining .replace methods. The latitude and longitdue were also sliced out of the Coordinates column and assigned each to their own respected columns.

In [5]:
london_boroughs = pd.read_csv('../data/raw/london_boroughs.csv', usecols=['Borough', 'Coordinates'])
london_boroughs['Latitude'] = london_boroughs['Coordinates'].str[43:50]
london_boroughs['Longitude'] = london_boroughs['Coordinates'].str[52:60]
london_boroughs['Borough'] = [b.replace('[note 1]', '').replace('[note 4]', '').replace('[note 2]', '') for b in london_boroughs['Borough'] ]
london_boroughs

Borough  \
0     Barking and Dagenham    
1                    Barnet   
2                    Bexley   
3                     Brent   
4                   Bromley   
5                    Camden   
6                   Croydon   
7                    Ealing   
8                   Enfield   
9                Greenwich    
10                  Hackney   
11  Hammersmith and Fulham    
12                 Haringey   
13                   Harrow   
14                 Havering   
15               Hillingdon   
16                 Hounslow   
17                Islington   
18   Kensington and Chelsea   
19     Kingston upon Thames   
20                  Lambeth   
21                 Lewisham   
22                   Merton   
23                   Newham   
24                Redbridge   
25     Richmond upon Thames   
26                Southwark   
27                   Sutton   
28            Tower Hamlets   
29           Waltham Forest   
30               Wandsworth   
31              Westminster   

                                          Coordinates Latitude Longitude  
0   51°33′39″N 0°09′21″E﻿,﻿51.5607°N 0.1557°E﻿,51....  51.5607  0.1557﻿   
1   51°37′31″N 0°09′06″W﻿,﻿51.6252°N 0.1517°W﻿,51....  51.6252  -0.1517﻿  
2   51°27′18″N 0°09′02″E﻿,﻿51.4549°N 0.1505°E﻿,51....  51.4549  0.1505﻿   
3   51°33′32″N 0°16′54″W﻿,﻿51.5588°N 0.2817°W﻿,51....  51.5588  -0.2817﻿  
4   51°24′14″N 0°01′11″E﻿,﻿51.4039°N 0.0198°E﻿,51....  51.4039  0.0198﻿   
5   51°31′44″N 0°07′32″W﻿,﻿51.5290°N 0.1255°W﻿,51....  51.5290  -0.1255﻿  
6   51°22′17″N 0°05′52″W﻿,﻿51.3714°N 0.0977°W﻿,51....  51.3714  -0.0977﻿  
7   51°30′47″N 0°18′32″W﻿,﻿51.5130°N 0.3089°W﻿,51....  51.5130  -0.3089﻿  
8   51°39′14″N 0°04′48″W﻿,﻿51.6538°N 0.0799°W﻿,51....  51.6538  -0.0799﻿  
9   51°29′21″N 0°03′53″E﻿,﻿51.4892°N 0.0648°E﻿,51....  51.4892  0.0648﻿   
10  51°32′42″N 0°03′19″W﻿,﻿51.5450°N 0.0553°W﻿,51....  51.5450  -0.0553﻿  
11  51°29′34″N 0°14′02″W﻿,﻿51.4927°N 0.2339°W﻿,51....  51.4927  -0.2339﻿  
12  51°36′00″N 0°06′43″W﻿,﻿51.6000°N 0.1119°W﻿,51....  51.6000  -0.1119﻿  
13  51°35′23″N 0°20′05″W﻿,﻿51.5898°N 0.3346°W﻿,51....  51.5898  -0.3346﻿  
14  51°34′52″N 0°11′01″E﻿,﻿51.5812°N 0.1837°E﻿,51....  51.5812  0.1837﻿   
15  51°32′39″N 0°28′34″W﻿,﻿51.5441°N 0.4760°W﻿,51....  51.5441  -0.4760﻿  
16  51°28′29″N 0°22′05″W﻿,﻿51.4746°N 0.3680°W﻿,51....  51.4746  -0.3680﻿  
17  51°32′30″N 0°06′08″W﻿,﻿51.5416°N 0.1022°W﻿,51....  51.5416  -0.1022﻿  
18  51°30′07″N 0°11′41″W﻿,﻿51.5020°N 0.1947°W﻿,51....  51.5020  -0.1947﻿  
19  51°24′31″N 0°18′23″W﻿,﻿51.4085°N 0.3064°W﻿,51....  51.4085  -0.3064﻿  
20  51°27′39″N 0°06′59″W﻿,﻿51.4607°N 0.1163°W﻿,51....  51.4607  -0.1163﻿  
21  51°26′43″N 0°01′15″W﻿,﻿51.4452°N 0.0209°W﻿,51....  51.4452  -0.0209﻿  
22  51°24′05″N 0°11′45″W﻿,﻿51.4014°N 0.1958°W﻿,51....  51.4014  -0.1958﻿  
23  51°30′28″N 0°02′49″E﻿,﻿51.5077°N 0.0469°E﻿,51....  51.5077  0.0469﻿   
24  51°33′32″N 0°04′27″E﻿,﻿51.5590°N 0.0741°E﻿,51....  51.5590  0.0741﻿   
25  51°26′52″N 0°19′34″W﻿,﻿51.4479°N 0.3260°W﻿,51....  51.4479  -0.3260﻿  
26  51°30′13″N 0°04′49″W﻿,﻿51.5035°N 0.0804°W﻿,51....  51.5035  -0.0804﻿  
27  51°21′42″N 0°11′40″W﻿,﻿51.3618°N 0.1945°W﻿,51....  51.3618  -0.1945﻿  
28  51°30′36″N 0°00′21″W﻿,﻿51.5099°N 0.0059°W﻿,51....  51.5099  -0.0059﻿  
29  51°35′27″N 0°00′48″W﻿,﻿51.5908°N 0.0134°W﻿,51....  51.5908  -0.0134﻿  
30  51°27′24″N 0°11′28″W﻿,﻿51.4567°N 0.1910°W﻿,51....  51.4567  -0.1910﻿  
31  51°29′50″N 0°08′14″W﻿,﻿51.4973°N 0.1372°W﻿,51....  51.4973  -0.1372﻿

#### Property and Rental Prices 

Next I scraped a list of London postcodes and their corresponding districts from the following website: https://www.doogal.co.uk/london_postcodes.php. Using the postcode I then scraped the average property prices and rental prices from the Foxton website. All the data is written into a CSV file.

In [27]:
with open('../data/raw/london_property_prices.csv', 'w', newline='', encoding='utf-8') as f:
    column_headers = ['postcode','districts', 'avg_property_price','avg_rental_price']
    writer = csv.DictWriter(f, fieldnames = column_headers)
    writer.writeheader()
    
    # Scrape postcodes and districts 
    source_postcode = requests.get('https://www.doogal.co.uk/london_postcodes.php').text
    soup1 = BeautifulSoup(source_postcode)
    districts = soup1.find('div', class_='realContent')
    a_elements = districts.find_all('a')[43:157]
    for i in range(len(a_elements)):
        Postcode = a_elements[i].getText().split(':')[0]
        Districts= a_elements[i].getText().split(': ')[1]
        i += 1
        
        # Scrape the prices for each postcode obtained above
        source_foxtons = requests.get('https://www.foxtons.co.uk/living-in/{}'.format(Postcode)).text
        soup2 = BeautifulSoup(source_foxtons)
        var_elements = soup2.find_all(['var'], class_="price_headline")
        property_price = var_elements[0].getText()[1:]
        rental_price = var_elements[1].getText()[1:]
        # Return NaN if there is no data for rental prices
        if len(rental_price) > 1:
            result = re.search('[0-9A-Fa-f,]+', rental_price).group()
        else:
            result = 'NaN'
            
        # Write all of the above into the CSV    
        writer.writerow({'postcode': Postcode, 'districts':Districts,
                         'avg_property_price':property_price, 'avg_rental_price':result})

In [28]:
london_property_prices = pd.read_csv('../data/raw/london_property_prices.csv')
london_property_prices.head()

postcode                       districts avg_property_price avg_rental_price
0       E1  Mile End, Stepney, Whitechapel            659,278              481
1       E2       Bethnal Green, Shoreditch            454,292              655
2       E3             Bow, Bromley-by-Bow            490,185              473
3       E4         Chingford, Highams Park            409,644              325
4       E5                         Clapton            662,577              514

### 2.3. Feature Selection 

From the Price Paid Data, most of the columns were dropped as they were not relevant in our business problem, such as TUID, Duration, PAON, SAON, Locality, PPD_Cat_Type and Record_Status. 

There were also a number of rows where the prices where very high, which could have been a commerical property. Therefore rows where the price is larger than £2,000,000 were also dropped.

In [4]:
ppd_2019_clean = ppd_2019.drop(columns=['TUID', 'Duration', 'PAON', 'SAON', 'Locality', 'PPD_Cat_Type', 'Record_Status'])

# Filter out rows where Town_City column contains 'LONDON'
ppd_london = ppd_2019_clean[ppd_2019['Town_City']=='LONDON']
ppd_london = ppd_london.drop(ppd_london[ppd_london.Price > 2000000].index)
ppd_london.head()

Price  Date_of_Transfer  Postcode Property_Type Old_New  \
918996  600000  2019-12-31 00:00  SW18 1UX             F       Y   
737743  600000  2019-12-31 00:00  SW18 1UX             F       Y   
737745  495000  2019-12-31 00:00  SW18 1UX             F       Y   
714996  600000  2019-12-31 00:00  SW18 1UX             F       Y   
956199  910000  2019-12-31 00:00   SE1 7HD             F       N   

                   Street Town_City    District          County  
918996        OSIERS ROAD    LONDON  WANDSWORTH  GREATER LONDON  
737743        OSIERS ROAD    LONDON  WANDSWORTH  GREATER LONDON  
737745        OSIERS ROAD    LONDON  WANDSWORTH  GREATER LONDON  
714996        OSIERS ROAD    LONDON  WANDSWORTH  GREATER LONDON  
956199  ALBERT EMBANKMENT    LONDON     LAMBETH  GREATER LONDON

In [5]:
ppd_grouped = ppd_london.groupby(['Street'])['Price'].mean().round(0).reset_index()
ppd_grouped.columns = ['street', 'avg_price']
ppd_grouped.sort_values(by=['avg_price'], inplace=True)
ppd_grouped

street  avg_price
9244        PEMBRIDGE ROAD      100.0
12772        WEYMOUTH MEWS      100.0
7179      LEESIDE CRESCENT      380.0
3756    DOWNS COURT PARADE     1000.0
900    BEACONSFIELD PARADE     1000.0
...                    ...        ...
7322            LINDEN LEA  2000000.0
6231          HOLYWELL ROW  2000000.0
5959      HERONDALE AVENUE  2000000.0
3173      CRAVEN HILL MEWS  2000000.0
9809         RANDOLPH MEWS  2000000.0

[13272 rows x 2 columns]

Now we filter out rows from the ppd_2019_clean dataframe where the Town is 'LONDON', then we group the dataframe by the street names and find the average price paid for property on those streets.

As there are a large number of rows, getting the latitude, longitude and FourSquare data for each row/street will take a significant amount of time. A Python script will be used to get all the latitude and longitude, write them to a CSV file, and the resulting dataset will then be separated into 4 bands based on the average price, increasing by £25,000 in the first three band and by £100,000 in the last band. 

This will decrease the computional time required and provide us with an overview of properties and their nearby venues across different pricing ranges.

In [6]:
ppd_london_2019 = pd.read_csv('../data/processed/ppd_london_2019.csv')
ppd_london_2019 = ppd_london_2019[ppd_london_2019.latitude != 'Nan']
ppd_london_2019.shape

(12610, 4)

In [7]:
ppd_london_2019['latitude'] = pd.to_numeric(ppd_london_2019['latitude'], downcast="float")
ppd_london_2019['longitude'] = pd.to_numeric(ppd_london_2019['longitude'], downcast="float")
ppd_london_2019.head()

street  avg_price   latitude  longitude
0    ABBESS CLOSE     296000  51.515453   0.049416
1  ABBEVILLE ROAD     613870  51.453304  -0.140988
2   ABBEY GARDENS    1473800  51.484844  -0.213365
3     ABBEY GROVE     350000  51.490322   0.115759
4    ABBEY PARADE     596200  51.531391  -0.292546

In [8]:
ppd_band1 = ppd_london_2019.query('(avg_price > 250000) & (avg_price <= 275000)')
ppd_band2 = ppd_london_2019.query('(avg_price > 500000) & (avg_price <= 525000)')
ppd_band3 = ppd_london_2019.query('(avg_price > 750000) & (avg_price <= 775000)')
ppd_band4 = ppd_london_2019.query('(avg_price > 1000000) & (avg_price <= 1100000)')

print(ppd_grouped.shape)
print('Band 1:', ppd_band1.shape)
print('Band 2:', ppd_band2.shape)
print('Band 3:', ppd_band3.shape)
print('Band 4:', ppd_band4.shape)

(13272, 2)
Band 1: (272, 4)
Band 2: (464, 4)
Band 3: (225, 4)
Band 4: (360, 4)


In [112]:
ppd_london_bands = ppd_band1.append([ppd_band2, ppd_band3, ppd_band4], ignore_index=True)
print(ppd_london_bands.shape)
ppd_london_bands.head()

(1321, 4)


street  avg_price   latitude  longitude
0  ABBEYFIELD ROAD     265000  51.491352  -0.053131
1      ACTON CLOSE     271000  51.627186  -0.061062
2  ALBATROSS CLOSE     265000  51.518841   0.058978
3   ALDWORTH GROVE     251000  51.451118  -0.014584
4   ALFREDA STREET     262250  51.474522  -0.150164

## 3. Exploratory Data Analysis (EDA)

### 3.1. Price Paid Data

Let's visualise the average property prices for those streets by plotting them on a map.

In [9]:
geolocator = Nominatim(user_agent='london_explorer')
location = geolocator.geocode('London, UK')
latitude_ldn = location.latitude
longitude_ldn = location.longitude
print('The geographical coordinate of London, UK are {}, {}.'.format(latitude_ldn, longitude_ldn))

The geographical coordinate of London, UK are 51.5073219, -0.1276474.


In [10]:
mapbox_access_token = (open("../secrets/mapbox_token.txt").read())

fig = px.scatter_mapbox(ppd_london_2019, lat="latitude", lon="longitude", size="avg_price", color="avg_price",
                  color_continuous_scale=px.colors.cyclical.IceFire, size_max=7)
fig.update_layout(
    title='Property Paid Price in London 2019',
    autosize=True,
    hovermode='closest',
    showlegend=True,
    mapbox=dict(
        accesstoken=mapbox_access_token,
        bearing=0,
        center=dict(
            lat=latitude_ldn,
            lon=longitude_ldn
        ),
        pitch=5,
        zoom=10,
        style='light'
    ),
)
fig.show()

As expected, neighbourhoods such as Mayfair, Chelsea, Knightsbridge, Notting Hill and Fulham have the highest average property prices. We can also see from the map above that more expensive properties are mostly located on the west side of central London, and compared to the east side there are far fewer properties that exceed the £1,000,000 mark. However there are exceptions, with a small cluster near Blackheath, Canary Wharf, Newbury Park and Bexleyheath.

This will be useful to home-buyers or investors as they may take into consideration a neighbourhood that they were not aware of previously. The next step would be to explore the said neighbourhoods using the FourSquare API.

### 3.2. Explore the area and nearby venues

Let's take a look at the first neighbourhood and it's nearby venues.

In [11]:
secret_dict = {}
with open('../secrets/foursquare_secrets.txt') as f:
    for item in f:
        (key, val) = item.split(':')
        secret_dict[key] = val.strip('\n')

In [43]:
LIMIT = 100
radius = 500
VERSION = '20180605'
neighborhood_latitude = ppd_london_2019.loc[7714, 'latitude']
neighborhood_longitude = ppd_london_2019.loc[7714, 'longitude']
neighborhood_name = ppd_london_2019.loc[7714, 'street']
url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(secret_dict.get('client_id'), secret_dict.get('client_secret'), neighborhood_latitude, neighborhood_longitude, VERSION, radius, LIMIT)
results = requests.get(url).json()

In [13]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [14]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = pd.json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues

name         categories        lat       lng
0                    Lidl        Supermarket  51.515982  0.054794
1            Costa Coffee        Coffee Shop  51.519691  0.049029
2  Dove Approach Bus Stop           Bus Stop  51.516429  0.046570
3                  Londis  Convenience Store  51.517176  0.045332
4   Beckton District Park               Park  51.514538  0.043280

In [15]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

5 venues were returned by Foursquare.


#### Now we repeat what we have done above for all the other neighbourhoods by creating a function that repeat the same process.

The function below takes in 3 variables and 1 default variable, it then loops over each row in the datafraem and sends the API call to FourSquare. The JSON data returned is then processed to extract the data that we are after, in this case they are Venue name, Venue latitude, Venue longitude and Venue category. Finally the data is written into a dataframe.

In [44]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            secret_dict.get('client_id'), 
            secret_dict.get('client_secret'), 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        try:
            results = requests.get(url).json()["response"]['groups'][0]['items']
        except:
            continue
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

Initially a for loop was using to run the function above over the 4 price band dataframes. However the script kept running into an error where the the key 'groups' was not found within the json response. Upon investigation this error, the function did not have an issue if the rows in question were isolated and the script re-ran, nor was it related to the FourSquare API rate limits. In the end, in order to overcome that error the function was ran separately on the 4 dataframes.

In [47]:
band1_venues = getNearbyVenues(names=ppd_band1['street'],
                            latitudes=ppd_band1['latitude'],
                            longitudes=ppd_band1['longitude']
                            )
band1_venues.groupby('Neighborhood')['Venue'].count()

ABBEYFIELD ROAD
ACTON CLOSE
ALBATROSS CLOSE
ALDWORTH GROVE
ALFREDA STREET
AMSTERDAM ROAD
ANTHONY ROAD
ARCH STREET
ARKLEY ROAD
AUCKLAND RISE
AVENUE GARDENS
AYRES CLOSE
BAILDON STREET
BARFIELD AVENUE
BARNEY CLOSE
BAROQUE GARDENS
BARROWFIELD CLOSE
BARSON CLOSE
BAYHAM PLACE
BEACON GATE
BEECH COURT
BELL GREEN LANE
BERNARD ASHLEY DRIVE
BERNWELL ROAD
BESANT WAY
BOLTON CRESCENT
BOUVERIE PLACE
BOWER STREET
BRAMHOPE LANE
BRANDON ESTATE
BRENDON GROVE
BRIXTON STATION ROAD
BROAD LANE
BROCKLEY VIEW
BROOK SQUARE
BRYMAY CLOSE
BUCKSTONE ROAD
BULWER COURT
BUTE STREET
BUXTON CLOSE
CAIRNS AVENUE
CAISTOR MEWS
CAMPSHILL ROAD
CANDLE STREET
CAPSTAN WAY
CAPULET SQUARE
CAROLINE CLOSE
CASTILE ROAD
CHADWIN ROAD
CHARDWELL CLOSE
CHERRY BLOSSOM CLOSE
CHESEMAN STREET
CHESTERTON TERRACE
CLARENCE LANE
CLEM ATTLEE COURT
CLIFF ROAD
CLIFFORD DRIVE
CLYSTON STREET
COATE STREET
COBORN ROAD
COE AVENUE
COLEBERT AVENUE
COLLIER CLOSE
COLYER CLOSE
CONGLETON GROVE
CONISTON CLOSE
COOKES CLOSE
COSGROVE CLOSE
COVERACK CLOSE
CRAVEN PA

Neighborhood
ABBEYFIELD ROAD           15
ACTON CLOSE               19
ALBATROSS CLOSE           11
ALDWORTH GROVE            15
ALFREDA STREET            23
                          ..
WOODLAND GROVE            29
WOOLWICH CHURCH STREET     4
WORSLEY BRIDGE ROAD        5
WYTHFIELD ROAD            22
YUNUS KHAN CLOSE          13
Name: Venue, Length: 271, dtype: int64

In [48]:
band2_venues = getNearbyVenues(names=ppd_band2['street'],
                            latitudes=ppd_band2['latitude'],
                            longitudes=ppd_band2['longitude']
                            )
band2_venues.groupby('Neighborhood')['Venue'].count()

ADDERLEY GROVE
ADMIRALS WAY
AGATON ROAD
ALBION ROAD
ALDIS STREET
ALEXANDRA DRIVE
AMBLER ROAD
ARCHERY STEPS
ARCHWAY MEWS
ARGYLE SQUARE
ARLOW ROAD
ARMOURY WAY
ARNOLD ROAD
ARRAN ROAD
ASH GROVE
ASH ROAD
ASHMORE CLOSE
ASPEN CLOSE
ASTBURY ROAD
ATHERFOLD ROAD
ATHOL SQUARE
AUCKLAND ROAD
AXMINSTER ROAD
BAKERS END
BALHAM GROVE
BALLARDS LANE
BANSTEAD GARDENS
BARRINGTON ROAD
BEACONSFIELD ROAD
BEECHFIELD ROAD
BELFORT ROAD
BELITHA VILLAS
BENHILL ROAD
BERESFORD AVENUE
BERTRAM ROAD
BEVERLEY COURT
BILLINGHURST WAY
BIRCHEN GROVE
BLACKTHORNE DRIVE
BLINCOE CLOSE
BLOMFIELD VILLAS
BLYTHE VALE
BODMIN STREET
BONNINGTON SQUARE
BOUNDARY ROAD
BOURNE GARDENS
BOYD STREET
BRAMCOTE GROVE
BRANCH PLACE
BRANDRAM ROAD
BRASSEY ROAD
BRAVINGTON ROAD
BREAKSPEARS ROAD
BREMER MEWS
BRENTMEAD PLACE
BRETT ROAD
BRIDGE LANE
BRIDGEWOOD ROAD
BRINDWOOD ROAD
BRITTON STREET
BROADWAY MARKET
BROWNS ROAD
BULLEN STREET
BUNYAN ROAD
BURNLEY ROAD
BYNE ROAD
BYRON ROAD
CADOGAN CLOSE
CADWALLON ROAD
CALDERON ROAD
CAMPBELL ROAD
CARLYLE ROAD
CARNAR

Neighborhood
ADDERLEY GROVE       9
ADMIRALS WAY         4
AGATON ROAD          7
ALBION ROAD         36
ALDIS STREET        25
                    ..
WOODCOTE AVENUE      9
WOODS ROAD          30
WOODSTOCK GROVE     83
WORCESTER AVENUE    17
WORSLEY ROAD         6
Name: Venue, Length: 461, dtype: int64

In [49]:
band3_venues = getNearbyVenues(names=ppd_band3['street'],
                            latitudes=ppd_band3['latitude'],
                            longitudes=ppd_band3['longitude']
                            )
band3_venues.groupby('Neighborhood')['Venue'].count()

ABBOTSHADE ROAD
ADOLPHUS ROAD
ALDENSLEY ROAD
ALLISON ROAD
AMBERDEN AVENUE
ANTILL ROAD
ARBERY ROAD
ARRAGON GARDENS
ASHBOURNE GROVE
ATTWOOD LANE
AUBERT PARK
AVENING ROAD
BARCLAY ROAD
BAXENDALE
BEAUCLERC ROAD
BEAUMONT STREET
BECKWITH ROAD
BELLEVUE ROAD
BERMONDSEY STREET
BEVERLEY ROAD
BEWDLEY STREET
BIRCHINGTON ROAD
BLOOMSBURY WAY
BONNEVILLE GARDENS
BOURNE HILL
BRAMPTON GROVE
BRATHWAY ROAD
BRIARBANK ROAD
BRIARFIELD AVENUE
BRISTON GROVE
BROCKLEY ROAD
BROWNING ROAD
BUCKINGHAM ROAD
CANNING CROSS
CARDINALS WAY
CATHERINE GROVE
CEDARHURST DRIVE
CHALFONT WAY
CHAMBERLAIN ROAD
CHAMBERLAYNE ROAD
CHANCELLORS WHARF
CHARLES STREET
CHASEFIELD ROAD
CHELSEA TOWERS
CHESSON ROAD
CHESTNUT DRIVE
CHEVERTON ROAD
CHISWICK HIGH ROAD
CHOUMERT ROAD
CHURCH WAY
CHURSTON GARDENS
CLAIRVIEW ROAD
CLIFTON ROAD
COLOSSEUM TERRACE
CONEY ACRE
COOPERS LANE
CORNTHWAITE ROAD
CORONET STREET
CRAVEN HILL GARDENS
CRAVEN ROAD
CULFORD ROAD
CYPRESS ROAD
CYPRUS ROAD
DALMENY ROAD
DARLASTON ROAD
DAVENANT STREET
DEERBROOK ROAD
DELAFORD STR

Neighborhood
ABBOTSHADE ROAD       15
ADOLPHUS ROAD         43
ALDENSLEY ROAD        51
AMBERDEN AVENUE        3
ANTILL ROAD           33
                      ..
WEST CROMWELL ROAD    36
WEST END LANE         13
WESTHOLM               4
WETHERELL ROAD        20
WIX'S LANE            19
Name: Venue, Length: 223, dtype: int64

In [50]:
band4_venues = getNearbyVenues(names=ppd_band4['street'],
                            latitudes=ppd_band4['latitude'],
                            longitudes=ppd_band4['longitude']
                            )
band4_venues.groupby('Neighborhood')['Venue'].count()

ACACIA ROAD
ACRIS STREET
AGAMEMNON ROAD
ALBERT BRIDGE ROAD
ALBION TERRACE
ALCONBURY ROAD
ALDBOURNE ROAD
ALLINGHAM MEWS
ALLOWAY ROAD
AMBROSE AVENUE
ANSON ROAD
ANTRIM ROAD
ANTROBUS ROAD
ASCOTT AVENUE
ASHCOMBE STREET
ASHEN GROVE
ASHER WAY
ASPLEY ROAD
BALDWIN TERRACE
BANGALORE STREET
BARONSMEDE
BATCHELOR STREET
BAYHAM STREET
BEAUVAL ROAD
BECMEAD AVENUE
BEDFORD AVENUE
BELLEVILLE ROAD
BELMONT GROVE
BELSIZE GROVE
BELSIZE PARK GARDENS
BENTHAL ROAD
BIDWELL GARDENS
BIRCHLANDS AVENUE
BLOEMFONTEIN AVENUE
BRACEY STREET
BRAMSHILL GARDENS
BRASENOSE DRIVE
BRAYFIELD TERRACE
BREWHOUSE YARD
BRIGHTLINGSEA PLACE
BROCKLEBANK ROAD
BROCKWELL PARK GARDENS
BROOKSBY STREET
BULWER STREET
BURLINGTON LANE
BURNFOOT AVENUE
BURNTHWAITE ROAD
BUTLERS & COLONIAL WHARF
CABUL ROAD
CADOGAN PLACE
CAIRN AVENUE
CANTER WAY
CHARLWOOD TERRACE
CHATSWORTH AVENUE
CHELMER ROAD
CHESTERFIELD GARDENS
CHETWODE ROAD
CHOUMERT GROVE
CHRISTCHURCH ROAD
CHURTON PLACE
CLAPTON TERRACE
CLARENDON DRIVE
CLAYLANDS ROAD
CLEVELAND GARDENS
CLEVELAND ST

Neighborhood
ACACIA ROAD            5
ACRIS STREET          15
AGAMEMNON ROAD         9
ALBERT BRIDGE ROAD    29
ALBION TERRACE        25
                      ..
WORLINGHAM ROAD       41
WORMHOLT ROAD         24
WORSHIP STREET        76
WROXHAM GARDENS        5
WYCOMBE PLACE         35
Name: Venue, Length: 358, dtype: int64

The 4 price band venues dataframes are appended to create 1 single dataframe, which is then pickled using the pandas .to_pickle method. This will eliminate the need to re-run the FourSquare venue calls above, thus saving time between runs.

In [170]:
london_venues = band1_venues.append([band2_venues, band3_venues, band4_venues], ignore_index=True)
london_venues.to_pickle('../data/processed/london_venues.pkl')  # saving the dataframe as a .pkl
print(london_venues.shape)
london_venues.head()

(30515, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  ABBEYFIELD ROAD              51.491352               -0.053131   
1  ABBEYFIELD ROAD              51.491352               -0.053131   
2  ABBEYFIELD ROAD              51.491352               -0.053131   
3  ABBEYFIELD ROAD              51.491352               -0.053131   
4  ABBEYFIELD ROAD              51.491352               -0.053131   

                           Venue  Venue Latitude  Venue Longitude  \
0  Fourpure Brewing Co. Tap Room       51.489105        -0.054053   
1                 Southwark Park       51.494990        -0.056538   
2                 EeBria Taproom       51.491332        -0.058978   
3               Partizan Brewery       51.491483        -0.057584   
4                 thelodge.space       51.494965        -0.050907   

         Venue Category  
0               Brewery  
1                  Park  
2              Beer Bar  
3               Brewery  
4  Gym / Fitness Center

In [63]:
print('There are {} unique categories.'.format(len(london_venues['Venue Category'].unique())))

There are 455 unique categories.


In [201]:
query = london_venues[london_venues['Neighborhood'] == 'WYCOMBE PLACE']
query

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
30480  WYCOMBE PLACE              51.454197               -0.186387   
30481  WYCOMBE PLACE              51.454197               -0.186387   
30482  WYCOMBE PLACE              51.454197               -0.186387   
30483  WYCOMBE PLACE              51.454197               -0.186387   
30484  WYCOMBE PLACE              51.454197               -0.186387   
...              ...                    ...                     ...   
30510  WYCOMBE PLACE              51.454197               -0.186387   
30511  WYCOMBE PLACE              51.454197               -0.186387   
30512  WYCOMBE PLACE              51.454197               -0.186387   
30513  WYCOMBE PLACE              51.454197               -0.186387   
30514  WYCOMBE PLACE              51.454197               -0.186387   

                                       Venue  Venue Latitude  Venue Longitude  \
30480                             Cafe Fleur       51.455728        -0.188987   
30481                             Press Café       51.457693        -0.184260   
30482                            Brewers Inn       51.456780        -0.189565   
30483                            Waterstones       51.454667        -0.192974   
30484                                Ekachai       51.454105        -0.193039   
...                                      ...             ...              ...   
30510                                Primark       51.455440        -0.193313   
30511              Southside Shopping Centre       51.455390        -0.192885   
30512                       Sainsbury's Café       51.454325        -0.191612   
30513                             Bus Stop N       51.457578        -0.189932   
30514  Wandsworth Common, Heathfield Gardens       51.453939        -0.179768   

         Venue Category  
30480              Café  
30481       Coffee Shop  
30482               Pub  
30483         Bookstore  
30484  Asian Restaurant  
...                 ...  
30510    Clothing Store  
30511     Shopping Mall  
30512              Café  
30513          Bus Stop  
30514              Park  

[35 rows x 7 columns]

### 3.3. Analysis each neighbourhood

In [104]:
# one hot encoding
pd.options.display.max_rows = 10
pd.options.display.max_columns = 20

london_onehot = pd.get_dummies(london_venues[['Venue Category']], prefix="", prefix_sep="")
# There was a 'Neighborhood' venue category which needed to be dropped as it was skewing the results
london_onehot.drop('Neighborhood', axis = 1, inplace=True)

# add neighborhood column back to dataframe as the first column
london_onehot.insert(loc=0, column='street', value=ppd_london_bands['street'])

print(london_onehot.shape)
london_onehot.head()

(30515, 455)


street  ATM  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  ABBEYFIELD ROAD    0                  0               0                  0   
1      ACTON CLOSE    0                  0               0                  0   
2  ALBATROSS CLOSE    0                  0               0                  0   
3   ALDWORTH GROVE    0                  0               0                  0   
4   ALFREDA STREET    0                  0               0                  0   

   African Restaurant  Airport Service  Airport Terminal  American Restaurant  \
0                   0                0                 0                    0   
1                   0                0                 0                    0   
2                   0                0                 0                    0   
3                   0                0                 0                    0   
4                   0                0                 0                    0   

   Animal Shelter  ...  Windmill  Wine Bar  Wine Shop  Winery  Wings Joint  \
0               0  ...         0         0          0       0            0   
1               0  ...         0         0          0       0            0   
2               0  ...         0         0          0       0            0   
3               0  ...         0         0          0       0            0   
4               0  ...         0         0          0       0            0   

   Women's Store  Xinjiang Restaurant  Yoga Studio  Yunnan Restaurant  Zoo  
0              0                    0            0                  0    0  
1              0                    0            0                  0    0  
2              0                    0            0                  0    0  
3              0                    0            0                  0    0  
4              0                    0            0                  0    0  

[5 rows x 455 columns]

In [106]:
london_onehot_grouped = london_onehot.groupby('street').mean().reset_index()

print(london_onehot_grouped.shape)
london_onehot_grouped

(1321, 455)


street  ATM  Accessories Store  Adult Boutique  \
0      ABBEYFIELD ROAD    0                  0               0   
1      ABBOTSHADE ROAD    0                  0               0   
2          ACACIA ROAD    0                  0               0   
3         ACRIS STREET    0                  0               0   
4          ACTON CLOSE    0                  0               0   
...                ...  ...                ...             ...   
1316      WORSLEY ROAD    0                  0               0   
1317   WROXHAM GARDENS    0                  0               0   
1318     WYCOMBE PLACE    0                  0               0   
1319    WYTHFIELD ROAD    0                  0               0   
1320  YUNUS KHAN CLOSE    0                  0               0   

      Afghan Restaurant  African Restaurant  Airport Service  \
0                     0                   0                0   
1                     0                   0                0   
2                     0                   0                0   
3                     0                   0                0   
4                     0                   0                0   
...                 ...                 ...              ...   
1316                  0                   0                0   
1317                  0                   0                0   
1318                  0                   0                0   
1319                  0                   0                0   
1320                  0                   0                0   

      Airport Terminal  American Restaurant  Animal Shelter  ...  Windmill  \
0                    0                    0               0  ...         0   
1                    0                    0               0  ...         0   
2                    0                    0               0  ...         0   
3                    0                    0               0  ...         0   
4                    0                    0               0  ...         0   
...                ...                  ...             ...  ...       ...   
1316                 0                    0               0  ...         0   
1317                 0                    0               0  ...         0   
1318                 0                    0               0  ...         0   
1319                 0                    0               0  ...         0   
1320                 0                    0               0  ...         0   

      Wine Bar  Wine Shop  Winery  Wings Joint  Women's Store  \
0            0          0       0            0              0   
1            0          0       0            0              0   
2            0          0       0            0              0   
3            0          0       0            0              0   
4            0          0       0            0              0   
...        ...        ...     ...          ...            ...   
1316         1          0       0            0              0   
1317         0          0       0            0              0   
1318         0          0       0            0              0   
1319         0          0       0            0              0   
1320         0          0       0            0              0   

      Xinjiang Restaurant  Yoga Studio  Yunnan Restaurant  Zoo  
0                       0            0                  0    0  
1                       0            0                  0    0  
2                       0            0                  0    0  
3                       0            0                  0    0  
4                       0            0                  0    0  
...                   ...          ...                ...  ...  
1316                    0            0                  0    0  
1317                    0            0                  0    0  
1318                    0            0                  0    0  
1319                    0            0                  0    0  
1320                 

#### Now we write a function to get the top 10 venues for each neighborhood

In [107]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [140]:
num_top_venues = 10

# for assigning indicators to 1st, 2nd & 3rd
indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['street']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['street'] = london_onehot_grouped['street']

for ind in np.arange(london_onehot_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(london_onehot_grouped.iloc[ind, :], num_top_venues)

print(neighborhoods_venues_sorted.shape)
neighborhoods_venues_sorted.head()

(1321, 11)


street     1st Most Common Venue 2nd Most Common Venue  \
0  ABBEYFIELD ROAD                   Brewery  Ethiopian Restaurant   
1  ABBOTSHADE ROAD            Ice Cream Shop                   Zoo   
2      ACACIA ROAD  Bike Rental / Bike Share  Ethiopian Restaurant   
3     ACRIS STREET                      Café                   Zoo   
4      ACTON CLOSE                      Park                   Zoo   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Event Space               Exhibit           Fabric Shop   
1     Fish & Chips Shop         Event Service           Event Space   
2           Event Space               Exhibit           Fabric Shop   
3  Ethiopian Restaurant           Event Space               Exhibit   
4              Fountain         Event Service           Event Space   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0               Factory    Falafel Restaurant                  Farm   
1               Exhibit           Fabric Shop               Factory   
2               Factory    Falafel Restaurant                  Farm   
3           Fabric Shop               Factory    Falafel Restaurant   
4               Exhibit           Fabric Shop               Factory   

  9th Most Common Venue 10th Most Common Venue  
0        Farmers Market   Fast Food Restaurant  
1    Falafel Restaurant                   Farm  
2        Farmers Market   Fast Food Restaurant  
3                  Farm         Farmers Market  
4    Falafel Restaurant                   Farm

In [193]:
neighborhoods_venues_sorted[neighborhoods_venues_sorted['street']=='WYCOMBE PLACE']

Cluster Labels         street 1st Most Common Venue  \
1318               0  WYCOMBE PLACE           Auto Garage   

     2nd Most Common Venue       3rd Most Common Venue 4th Most Common Venue  \
1318                   Zoo  Financial or Legal Service         Event Service   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
1318           Event Space               Exhibit           Fabric Shop   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
1318               Factory    Falafel Restaurant                   Farm

## 4. Modeling

### 4.1. K-Means Clustering

In [139]:
# set number of clusters
kclusters = 12

ppd_grouped_clustering = london_onehot_grouped.drop('street', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(ppd_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]
# neighborhoods_venues_sorted = []

array([ 6,  0,  0,  4, 11,  0,  0,  0,  0,  0])

In [141]:
# add clustering labels
neighborhoods_venues_sorted.insert(loc = 0, column = 'Cluster Labels', value = kmeans.labels_)
neighborhoods_venues_sorted

ppd_london_merged = ppd_london_bands

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
ppd_london_merged = ppd_london_merged.join(neighborhoods_venues_sorted.set_index('street'), on='street')

ppd_london_merged.head() # check the last columns!

street  avg_price   latitude  longitude  Cluster Labels  \
0  ABBEYFIELD ROAD     265000  51.491352  -0.053131               6   
1      ACTON CLOSE     271000  51.627186  -0.061062              11   
2  ALBATROSS CLOSE     265000  51.518841   0.058978               0   
3   ALDWORTH GROVE     251000  51.451118  -0.014584               6   
4   ALFREDA STREET     262250  51.474522  -0.150164               0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0               Brewery  Ethiopian Restaurant           Event Space   
1                  Park                   Zoo              Fountain   
2              Beer Bar                   Zoo  Ethiopian Restaurant   
3               Brewery  Ethiopian Restaurant           Event Space   
4  Gym / Fitness Center                   Zoo  Ethiopian Restaurant   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0               Exhibit           Fabric Shop               Factory   
1         Event Service           Event Space               Exhibit   
2           Event Space               Exhibit           Fabric Shop   
3               Exhibit           Fabric Shop               Factory   
4           Event Space               Exhibit           Fabric Shop   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0    Falafel Restaurant                  Farm        Farmers Market   
1           Fabric Shop               Factory    Falafel Restaurant   
2               Factory    Falafel Restaurant                  Farm   
3    Falafel Restaurant                  Farm        Farmers Market   
4               Factory    Falafel Restaurant                  Farm   

  10th Most Common Venue  
0   Fast Food Restaurant  
1                   Farm  
2         Farmers Market  
3   Fast Food Restaurant  
4         Farmers Market

In [142]:
# create map
map_clusters = folium.Map(location=[latitude_ldn, longitude_ldn], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(ppd_london_merged['latitude'], ppd_london_merged['longitude'], ppd_london_merged['street'], ppd_london_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [152]:
ppd_london_merged.loc[ppd_london_merged['Cluster Labels'] == 0, ppd_london_merged.columns[[0,1] + list(range(5, ppd_london_merged.shape[1]))]]

street  avg_price 1st Most Common Venue 2nd Most Common Venue  \
2     ALBATROSS CLOSE     265000              Beer Bar                   Zoo   
4      ALFREDA STREET     262250  Gym / Fitness Center                   Zoo   
5      AMSTERDAM ROAD     264500                   Bar                   Zoo   
6        ANTHONY ROAD     250600       Thai Restaurant                   Zoo   
8         ARKLEY ROAD     257667                Bakery                   Zoo   
...               ...        ...                   ...                   ...   
1314    WOODLAND RISE    1073333    Athletics & Sports                   Zoo   
1316  WORLINGHAM ROAD    1095000  Gym / Fitness Center                   Zoo   
1317    WORMHOLT ROAD    1060333    Light Rail Station                   Zoo   
1318   WORSHIP STREET    1044885     Convenience Store                   Zoo   
1320    WYCOMBE PLACE    1025000           Auto Garage                   Zoo   

           3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
2           Ethiopian Restaurant           Event Space               Exhibit   
4           Ethiopian Restaurant           Event Space               Exhibit   
5           Ethiopian Restaurant           Event Space               Exhibit   
6          Entertainment Service         Event Service           Event Space   
8           Ethiopian Restaurant           Event Space               Exhibit   
...                          ...                   ...                   ...   
1314  Financial or Legal Service         Event Service           Event Space   
1316        Ethiopian Restaurant           Event Space               Exhibit   
1317  Financial or Legal Service         Event Service           Event Space   
1318           Fish & Chips Shop         Event Service           Event Space   
1320  Financial or Legal Service         Event Service           Event Space   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
2              Fabric Shop               Factory    Falafel Restaurant   
4              Fabric Shop               Factory    Falafel Restaurant   
5              Fabric Shop               Factory    Falafel Restaurant   
6                  Exhibit           Fabric Shop               Factory   
8              Fabric Shop               Factory    Falafel Restaurant   
...                    ...                   ...                   ...   
1314               Exhibit           Fabric Shop               Factory   
1316           Fabric Shop               Factory    Falafel Restaurant   
1317               Exhibit           Fabric Shop               Factory   
1318               Exhibit           Fabric Shop               Factory   
1320               Exhibit           Fabric Shop               Factory   

     9th Most Common Venue 10th Most Common Venue  
2                     Farm         Farmers Market  
4                     Farm         Farmers Market  
5                     Farm         Farmers Market  
6       Falafel Restaurant                   Farm  
8                     Farm         Farmers Market  
...                    ...                    ...  
1314    Falafel Restaurant                   Farm  
1316                  Farm         Farmers Market  
1317    Falafel Restaurant                   Farm  
1318    Falafel Restaurant                   Farm  
1320    Falafel Restaurant                   Farm  

[883 rows x 12 columns]

In [153]:
ppd_london_merged.loc[ppd_london_merged['Cluster Labels'] == 1, ppd_london_merged.columns[[0,1] + list(range(5, ppd_london_merged.shape[1]))]]

street  avg_price 1st Most Common Venue  \
35            BRYMAY CLOSE     255000           Supermarket   
39            BUXTON CLOSE     255000           Supermarket   
45          CAPULET SQUARE     260000           Supermarket   
90         FRAMPTON STREET     270000           Supermarket   
113           HAYNES CLOSE     270833           Supermarket   
...                    ...        ...                   ...   
981             BARONSMEDE    1037500           Supermarket   
985         BECMEAD AVENUE    1078699           Supermarket   
1015          CHELMER ROAD    1008833           Supermarket   
1016  CHESTERFIELD GARDENS    1014611           Supermarket   
1297           WARPLE MEWS    1040000           Supermarket   

     2nd Most Common Venue       3rd Most Common Venue 4th Most Common Venue  \
35                     Zoo  Financial or Legal Service         Event Service   
39                     Zoo  Financial or Legal Service         Event Service   
45                     Zoo  Financial or Legal Service         Event Service   
90                     Zoo  Financial or Legal Service         Event Service   
113                    Zoo  Financial or Legal Service         Event Service   
...                    ...                         ...                   ...   
981                    Zoo  Financial or Legal Service         Event Service   
985                    Zoo  Financial or Legal Service         Event Service   
1015                   Zoo  Financial or Legal Service         Event Service   
1016                   Zoo  Financial or Legal Service         Event Service   
1297                   Zoo  Financial or Legal Service         Event Service   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
35             Event Space               Exhibit           Fabric Shop   
39             Event Space               Exhibit           Fabric Shop   
45             Event Space               Exhibit           Fabric Shop   
90             Event Space               Exhibit           Fabric Shop   
113            Event Space               Exhibit           Fabric Shop   
...                    ...                   ...                   ...   
981            Event Space               Exhibit           Fabric Shop   
985            Event Space               Exhibit           Fabric Shop   
1015           Event Space               Exhibit           Fabric Shop   
1016           Event Space               Exhibit           Fabric Shop   
1297           Event Space               Exhibit           Fabric Shop   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
35                 Factory    Falafel Restaurant                   Farm  
39                 Factory    Falafel Restaurant                   Farm  
45                 Factory    Falafel Restaurant                   Farm  
90                 Factory    Falafel Restaurant                   Farm  
113                Factory    Falafel Restaurant                   Farm  
...                    ...                   ...                    ...  
981                Factory    Falafel Restaurant                   Farm  
985                Factory    Falafel Restaurant                   Farm  
1015               Factory    Falafel Restaurant                   Farm  
1016               Factory    Falafel Restaurant                   Farm  
1297               Factory    Falafel Restaurant                   Farm  

[26 rows x 12 columns]

In [155]:
ppd_london_merged.loc[ppd_london_merged['Cluster Labels'] == 2, ppd_london_merged.columns[[0,1] + list(range(5, ppd_london_merged.shape[1]))]]

street  avg_price 1st Most Common Venue  \
56           CLIFFORD DRIVE     275000     Indian Restaurant   
88          FESTUBERT PLACE     274417     Indian Restaurant   
92             GARETH DRIVE     254500     Indian Restaurant   
110         GRITTLETON ROAD     269417     Indian Restaurant   
169        NINE ACRES CLOSE     275000     Indian Restaurant   
...                     ...        ...                   ...   
968          ALLINGHAM MEWS    1080000     Indian Restaurant   
1042          CRESCENT LANE    1045050     Indian Restaurant   
1140  KENSINGTON COURT MEWS    1100000     Indian Restaurant   
1142        KIDBROOKE GROVE    1053111     Indian Restaurant   
1219         RITCHIE STREET    1050000     Indian Restaurant   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
56                     Zoo     Fish & Chips Shop         Event Service   
88                     Zoo     Fish & Chips Shop         Event Service   
92                     Zoo     Fish & Chips Shop         Event Service   
110                    Zoo     Fish & Chips Shop         Event Service   
169                    Zoo     Fish & Chips Shop         Event Service   
...                    ...                   ...                   ...   
968                    Zoo     Fish & Chips Shop         Event Service   
1042                   Zoo     Fish & Chips Shop         Event Service   
1140                   Zoo     Fish & Chips Shop         Event Service   
1142                   Zoo     Fish & Chips Shop         Event Service   
1219                   Zoo     Fish & Chips Shop         Event Service   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
56             Event Space               Exhibit           Fabric Shop   
88             Event Space               Exhibit           Fabric Shop   
92             Event Space               Exhibit           Fabric Shop   
110            Event Space               Exhibit           Fabric Shop   
169            Event Space               Exhibit           Fabric Shop   
...                    ...                   ...                   ...   
968            Event Space               Exhibit           Fabric Shop   
1042           Event Space               Exhibit           Fabric Shop   
1140           Event Space               Exhibit           Fabric Shop   
1142           Event Space               Exhibit           Fabric Shop   
1219           Event Space               Exhibit           Fabric Shop   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
56                 Factory    Falafel Restaurant                   Farm  
88                 Factory    Falafel Restaurant                   Farm  
92                 Factory    Falafel Restaurant                   Farm  
110                Factory    Falafel Restaurant                   Farm  
169                Factory    Falafel Restaurant                   Farm  
...                    ...                   ...                    ...  
968                Factory    Falafel Restaurant                   Farm  
1042               Factory    Falafel Restaurant                   Farm  
1140               Factory    Falafel Restaurant                   Farm  
1142               Factory    Falafel Restaurant                   Farm  
1219               Factory    Falafel Restaurant                   Farm  

[20 rows x 12 columns]

In [162]:
ppd_london_merged.loc[ppd_london_merged['Cluster Labels'] == 3, ppd_london_merged.columns[[0,1,2,3
                                                    ] + list(range(5, ppd_london_merged.shape[1]))]]

street  avg_price   latitude  longitude  \
14          BARNEY CLOSE     258750  51.487480   0.033208   
44           CAPSTAN WAY     273500  51.503357  -0.035382   
52    CHESTERTON TERRACE     270938  51.528610   0.022977   
72            DALING WAY     269667  51.533783  -0.036247   
73         DEFENCE CLOSE     255000  51.503746   0.089403   
...                  ...        ...        ...        ...   
1251        ST ELMO ROAD    1050000  51.504425  -0.244524   
1254         STABLE WALK    1016512  51.512981  -0.068963   
1269         TASMAN ROAD    1011667  51.465179  -0.125115   
1290       TRINITY CLOSE    1063833  51.563919   0.006890   
1303      WESTHORPE ROAD    1060000  51.466579  -0.224367   

     1st Most Common Venue 2nd Most Common Venue       3rd Most Common Venue  \
14                     Pub                   Zoo  Financial or Legal Service   
44                     Pub                   Zoo  Financial or Legal Service   
52                     Pub                   Zoo  Financial or Legal Service   
72                     Pub                   Zoo  Financial or Legal Service   
73                     Pub                   Zoo  Financial or Legal Service   
...                    ...                   ...                         ...   
1251                   Pub                   Zoo  Financial or Legal Service   
1254                   Pub                   Zoo  Financial or Legal Service   
1269                   Pub                   Zoo  Financial or Legal Service   
1290                   Pub                   Zoo  Financial or Legal Service   
1303                   Pub                   Zoo  Financial or Legal Service   

     4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
14           Event Service           Event Space               Exhibit   
44           Event Service           Event Space               Exhibit   
52           Event Service           Event Space               Exhibit   
72           Event Service           Event Space               Exhibit   
73           Event Service           Event Space               Exhibit   
...                    ...                   ...                   ...   
1251         Event Service           Event Space               Exhibit   
1254         Event Service           Event Space               Exhibit   
1269         Event Service           Event Space               Exhibit   
1290         Event Service           Event Space               Exhibit   
1303         Event Service           Event Space               Exhibit   

     7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
14             Fabric Shop               Factory    Falafel Restaurant   
44             Fabric Shop               Factory    Falafel Restaurant   
52             Fabric Shop               Factory    Falafel Restaurant   
72             Fabric Shop               Factory    Falafel Restaurant   
73             Fabric Shop               Factory    Falafel Restaurant   
...                    ...                   ...                   ...   
1251           Fabric Shop               Factory    Falafel Restaurant   
1254           Fabric Shop               Factory    Falafel Restaurant   
1269           Fabric Shop               Factory    Falafel Restaurant   
1290           Fabric Shop               Factory    Falafel Restaurant   
1303           Fabric Shop               Factory    Falafel Restaurant   

     10th Most Common Venue  
14                     Farm  
44                     Farm  
52                     Farm  
72                     Farm  
73                     Farm  
...                     ...  
1251                   Farm  
1254                   Farm  
1269                   Farm  
1290                   Farm  
1303                   Farm  

[82 rows x 14 columns]

In [164]:
test_latitude = 51.504425
test_longitude = -0.244524
test_name = 'ST ELMO ROAD'
urltest = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(secret_dict.get('client_id'), secret_dict.get('client_secret'), test_latitude, test_longitude, VERSION, radius, LIMIT)
resultstest = requests.get(urltest).json()
resultstest

{'meta': {'code': 200, 'requestId': '5ec7059814a126001cdc5274'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Askew',
  'headerFullLocation': 'Askew, London',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 35,
  'suggestedBounds': {'ne': {'lat': 51.5089250045,
    'lng': -0.23730804334817682},
   'sw': {'lat': 51.499924995499995, 'lng': -0.2517399566518232}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4fb18491e4b0bb3b415eb877',
       'name': 'Detour Café',
       'location': {'address': '135 Askew Rd',
        'lat': 51.50244,
        'lng': -0.24260111,
        'labeledLatLngs': [{'label': 'display',
          'lat': 51.50244,
          'lng': -0.2426011

In [166]:
venues = resultstest['response']['groups'][0]['items']
    
nearby_venues_test = pd.json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues_test =nearby_venues_test.loc[:, filtered_columns]

# filter the category for each row
nearby_venues_test['venue.categories'] = nearby_venues_test.apply(get_category_type, axis=1)

# clean columns
nearby_venues_test.columns = [col.split(".")[-1] for col in nearby_venues_test.columns]

nearby_venues_test

name                 categories        lat       lng
0             Detour Café                       Café  51.502440 -0.242601
1         Sufi Restaurant  Middle Eastern Restaurant  51.504070 -0.243703
2             Adam's Cafe        Moroccan Restaurant  51.504093 -0.243444
3               Happy Sky                     Bakery  51.503254 -0.243488
4           Som Tam House            Thai Restaurant  51.502500 -0.242672
..                    ...                        ...        ...       ...
30  First Avenue Bus Stop                   Bus Stop  51.506801 -0.246157
31       Oriental Express         Chinese Restaurant  51.506606 -0.246828
32    Chilli Spice & Wine          Indian Restaurant  51.506744 -0.246574
33    West One Guesthouse                      Hotel  51.504132 -0.239130
34     Five Star Fish Bar       Fast Food Restaurant  51.506450 -0.239950

[35 rows x 4 columns]

### 4.2. HDBSCAN

## 5. Conclusions

## Bits of code

In [ ]:
# Get unique street names from the new ppd_london dataframe, remove nan values.
ppd_london_streets = [x for x in ppd_london['Street'].unique() if str(x) != 'nan']
ppd_london_streets[0:10]

## References

How to access HM Land Registry Price Paid Data: https://www.gov.uk/guidance/about-the-price-paid-data

Price Paid Data - HM Land Registry: https://www.gov.uk/government/statistical-data-sets/price-paid-data-downloads

Average private rental prices per borough:https://data.london.gov.uk/dataset/average-private-rents-borough

Borough property and rental prices - Foxtons: https://www.foxtons.co.uk/living-in/bermondsey

List of London boroughs : https://en.wikipedia.org/wiki/List_of_London_boroughs